In [2]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover
import numpy as np
import pandas as pd
from datetime import datetime, timedelta
import matplotlib.pyplot as plt
import json
from pathlib import Path
import alpaca_trade_api as tradeapi
import requests
import os 
from dotenv import load_dotenv

%matplotlib inline


from backtesting.test import SMA




/Users/bulya/opt/anaconda3/envs/vizenv/lib/python3.7/site-packages/backtesting/_plotting.py:44: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

In [3]:
load_dotenv()

alpaca_api_key = os.getenv("Api_key")
alpaca_secret_key = os.getenv("Secret_Key")

api = tradeapi.REST(alpaca_api_key, alpaca_secret_key, api_version='v2')


type(alpaca_api_key)


str

In [4]:
finance_sector = api.alpha_vantage.historic_quotes('XLF', adjusted=True, output_format='pandas')
finance_sector.head()

1. open  2. high   3. low  4. close  5. adjusted close  \
date                                                                 
2020-05-01    22.25   22.310  21.9115     22.06              22.06   
2020-04-30    22.91   23.160  22.6750     22.79              22.79   
2020-04-29    23.42   23.655  23.1800     23.38              23.38   
2020-04-28    23.16   23.325  22.6700     22.72              22.72   
2020-04-27    21.96   22.600  21.9200     22.48              22.48   

              6. volume  7. dividend amount  8. split coefficient  
date                                                               
2020-05-01   37519690.0                 0.0                   1.0  
2020-04-30   56730669.0                 0.0                   1.0  
2020-04-29   70050222.0                 0.0                   1.0  
2020-04-28   46430248.0                 0.0                   1.0  
2020-04-27  109428235.0                 0.0                   1.0

In [5]:
finance_sector.columns

Index(['1. open', '2. high', '3. low', '4. close', '5. adjusted close',
       '6. volume', '7. dividend amount', '8. split coefficient'],
      dtype='object')

In [6]:
finance_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
finance_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)
finance_sector

Open    High      Low    Close       Volume
date                                                    
2020-05-01  22.25  22.310  21.9115  22.0600   37519690.0
2020-04-30  22.91  23.160  22.6750  22.7900   56730669.0
2020-04-29  23.42  23.655  23.1800  23.3800   70050222.0
2020-04-28  23.16  23.325  22.6700  22.7200   46430248.0
2020-04-27  21.96  22.600  21.9200  22.4800  109428235.0
...           ...     ...      ...      ...          ...
2000-05-05  22.69  23.160  22.6600  12.4970      60500.0
2000-05-04  23.13  23.190  22.7800  12.4158     146900.0
2000-05-03  23.78  23.980  23.0900  12.6106     345500.0
2000-05-02  23.69  23.940  23.6400  12.8380     145800.0
2000-05-01  23.38  24.280  23.3400  12.9624      95100.0

[5033 rows x 5 columns]

In [7]:
finance_sector.sort_index(ascending=True, inplace=True)
finance_sector

Open    High      Low    Close       Volume
date                                                    
2000-05-01  23.38  24.280  23.3400  12.9624      95100.0
2000-05-02  23.69  23.940  23.6400  12.8380     145800.0
2000-05-03  23.78  23.980  23.0900  12.6106     345500.0
2000-05-04  23.13  23.190  22.7800  12.4158     146900.0
2000-05-05  22.69  23.160  22.6600  12.4970      60500.0
...           ...     ...      ...      ...          ...
2020-04-27  21.96  22.600  21.9200  22.4800  109428235.0
2020-04-28  23.16  23.325  22.6700  22.7200   46430248.0
2020-04-29  23.42  23.655  23.1800  23.3800   70050222.0
2020-04-30  22.91  23.160  22.6750  22.7900   56730669.0
2020-05-01  22.25  22.310  21.9115  22.0600   37519690.0

[5033 rows x 5 columns]

In [20]:
finance_sector.isnull().sum()
finance_sector.dropna()



Open    High      Low    Close       Volume
date                                                    
2000-05-01  23.38  24.280  23.3400  12.9624      95100.0
2000-05-02  23.69  23.940  23.6400  12.8380     145800.0
2000-05-03  23.78  23.980  23.0900  12.6106     345500.0
2000-05-04  23.13  23.190  22.7800  12.4158     146900.0
2000-05-05  22.69  23.160  22.6600  12.4970      60500.0
...           ...     ...      ...      ...          ...
2020-04-27  21.96  22.600  21.9200  22.4800  109428235.0
2020-04-28  23.16  23.325  22.6700  22.7200   46430248.0
2020-04-29  23.42  23.655  23.1800  23.3800   70050222.0
2020-04-30  22.91  23.160  22.6750  22.7900   56730669.0
2020-05-01  22.25  22.310  21.9115  22.0600   37519690.0

[5033 rows x 5 columns]

In [21]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()


bt = Backtest(finance_sector, SmaCross,
              cash=10000, commission=.002)
bt.run()


Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          98.9733
Equity Final [$]                      1571.88
Equity Peak [$]                       14896.2
Return [%]                           -84.2812
Buy & Hold Return [%]                 70.1845
Max. Drawdown [%]                    -91.0972
Avg. Drawdown [%]                     -52.713
Max. Drawdown Duration     7156 days 00:00:00
Avg. Drawdown Duration     2418 days 00:00:00
# Trades                                  277
Win Rate [%]                           34.657
Best Trade [%]                        47.0293
Worst Trade [%]                      -22.7831
Avg. Trade [%]                      -0.482892
Max. Trade Duration         128 days 00:00:00
Avg. Trade Duration          27 days 00:00:00
Expectancy [%]                        4.72939
SQN                                  -1.89957
Sharpe Ratio                      

In [22]:
bt.plot()

In [23]:
energy_sector = api.alpha_vantage.historic_quotes('XLE', adjusted=True, output_format='pandas')
energy_sector.head()

1. open  2. high   3. low  4. close  5. adjusted close  \
date                                                                 
2020-05-01    37.22    37.50  35.4100     35.85              35.85   
2020-04-30    39.08    39.08  37.4400     38.00              38.00   
2020-04-29    37.37    38.99  37.3400     38.86              38.86   
2020-04-28    35.90    36.40  35.3200     36.18              36.18   
2020-04-27    34.36    35.62  33.5758     35.37              35.37   

             6. volume  7. dividend amount  8. split coefficient  
date                                                              
2020-05-01  29261679.0                 0.0                   1.0  
2020-04-30  41995005.0                 0.0                   1.0  
2020-04-29  35468877.0                 0.0                   1.0  
2020-04-28  29565660.0                 0.0                   1.0  
2020-04-27  23275823.0                 0.0                   1.0

In [24]:
energy_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
energy_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)

In [25]:
energy_sector.sort_index(ascending=True, inplace=True)

In [26]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()


bt = Backtest(energy_sector, SmaCross,
              cash=10000, commission=.002)
bt.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          99.1786
Equity Final [$]                      2597.59
Equity Peak [$]                       13482.1
Return [%]                           -74.0241
Buy & Hold Return [%]                 91.8118
Max. Drawdown [%]                    -88.6938
Avg. Drawdown [%]                    -44.3546
Max. Drawdown Duration     7266 days 00:00:00
Avg. Drawdown Duration     3634 days 00:00:00
# Trades                                  285
Win Rate [%]                          32.9825
Best Trade [%]                        48.6776
Worst Trade [%]                      -17.2769
Avg. Trade [%]                      -0.262811
Max. Trade Duration         184 days 00:00:00
Avg. Trade Duration          26 days 00:00:00
Expectancy [%]                        4.37447
SQN                                  -1.44421
Sharpe Ratio                      

In [27]:
bt.plot()

In [31]:
materials_sector = api.alpha_vantage.historic_quotes('XLB', adjusted=True, output_format='pandas')


In [32]:
materials_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
materials_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)


In [33]:
materials_sector.sort_index(ascending=True, inplace=True)


In [34]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()


bt = Backtest(materials_sector, SmaCross,
              cash=10000, commission=.002)
bt.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          99.2608
Equity Final [$]                      538.094
Equity Peak [$]                       14345.4
Return [%]                           -94.6191
Buy & Hold Return [%]                 267.583
Max. Drawdown [%]                    -96.9868
Avg. Drawdown [%]                     -16.839
Max. Drawdown Duration     7245 days 00:00:00
Avg. Drawdown Duration     1212 days 00:00:00
# Trades                                  293
Win Rate [%]                          31.7406
Best Trade [%]                        28.3216
Worst Trade [%]                       -17.589
Avg. Trade [%]                      -0.887017
Max. Trade Duration          98 days 00:00:00
Avg. Trade Duration          25 days 00:00:00
Expectancy [%]                        3.82947
SQN                                  -3.34582
Sharpe Ratio                      

In [35]:
bt.plot()

In [36]:
industrial_sector = api.alpha_vantage.historic_quotes('XLI', adjusted=True, output_format='pandas')
industrial_sector.head()

1. open  2. high  3. low  4. close  5. adjusted close   6. volume  \
date                                                                            
2020-05-01    63.08    63.25  61.855     62.27              62.27   9019215.0   
2020-04-30    64.60    64.72  63.735     64.21              64.21  14309803.0   
2020-04-29    65.57    66.22  64.920     65.51              65.51  12756940.0   
2020-04-28    64.34    65.01  63.610     64.28              64.28   9938556.0   
2020-04-27    62.00    63.49  61.880     63.10              63.10   9323240.0   

            7. dividend amount  8. split coefficient  
date                                                  
2020-05-01                 0.0                   1.0  
2020-04-30                 0.0                   1.0  
2020-04-29                 0.0                   1.0  
2020-04-28                 0.0                   1.0  
2020-04-27                 0.0                   1.0

In [37]:
industrial_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
industrial_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)

In [40]:
industrial_sector.sort_index(ascending=True, inplace=True)


In [41]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()


bt = Backtest(industrial_sector, SmaCross,
              cash=10000, commission=.002)
bt.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          99.2471
Equity Final [$]                      2957.45
Equity Peak [$]                       16894.9
Return [%]                           -70.4255
Buy & Hold Return [%]                 201.012
Max. Drawdown [%]                     -85.109
Avg. Drawdown [%]                    -29.6736
Max. Drawdown Duration     3992 days 00:00:00
Avg. Drawdown Duration      807 days 00:00:00
# Trades                                  267
Win Rate [%]                          34.4569
Best Trade [%]                        26.8158
Worst Trade [%]                      -14.9035
Avg. Trade [%]                      -0.279413
Max. Trade Duration         114 days 00:00:00
Avg. Trade Duration          28 days 00:00:00
Expectancy [%]                        3.70131
SQN                                 -0.938665
Sharpe Ratio                      

In [42]:
bt.plot()

In [44]:
consumer_discret_sector = api.alpha_vantage.historic_quotes('XLY', adjusted=True, output_format='pandas')


In [46]:
consumer_discret_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
consumer_discret_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)

In [47]:
consumer_discret_sector.sort_index(ascending=True, inplace=True)

In [49]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()


bt_consumer_d = Backtest(consumer_discret_sector, SmaCross,
              cash=10000, commission=.002)
bt_consumer_d.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          98.7132
Equity Final [$]                      1519.98
Equity Peak [$]                       11916.6
Return [%]                           -84.8002
Buy & Hold Return [%]                 389.345
Max. Drawdown [%]                    -89.6174
Avg. Drawdown [%]                    -24.4721
Max. Drawdown Duration     7183 days 00:00:00
Avg. Drawdown Duration     1447 days 00:00:00
# Trades                                  262
Win Rate [%]                          35.4962
Best Trade [%]                        22.7121
Worst Trade [%]                      -18.1016
Avg. Trade [%]                      -0.562577
Max. Trade Duration         126 days 00:00:00
Avg. Trade Duration          28 days 00:00:00
Expectancy [%]                        3.77455
SQN                                  -2.46725
Sharpe Ratio                      

In [50]:
bt_consumer_d.plot()

In [54]:
consumer_staples_sector = api.alpha_vantage.historic_quotes('XLP', adjusted=True, output_format='pandas')


In [55]:
consumer_staples_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
consumer_staples_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)

In [56]:
consumer_staples_sector.sort_index(ascending=True, inplace=True)

In [57]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()


bt_consumer_s = Backtest(consumer_staples_sector, SmaCross,
              cash=10000, commission=.002)
bt_consumer_s.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          99.1513
Equity Final [$]                       4348.7
Equity Peak [$]                       15244.5
Return [%]                            -56.513
Buy & Hold Return [%]                 304.635
Max. Drawdown [%]                    -74.3951
Avg. Drawdown [%]                    -19.2304
Max. Drawdown Duration     6423 days 00:00:00
Avg. Drawdown Duration      559 days 00:00:00
# Trades                                  265
Win Rate [%]                          33.5849
Best Trade [%]                        17.5119
Worst Trade [%]                      -11.5152
Avg. Trade [%]                      -0.204568
Max. Trade Duration         140 days 00:00:00
Avg. Trade Duration          28 days 00:00:00
Expectancy [%]                        2.32295
SQN                                  -1.42003
Sharpe Ratio                      

In [59]:
bt_consumer_s.plot()

In [61]:
utilities_sector = api.alpha_vantage.historic_quotes('XLU', adjusted=True, output_format='pandas')


In [62]:
utilities_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
utilities_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)

In [63]:
utilities_sector.sort_index(ascending=True, inplace=True)

In [64]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()

bt_utilities = Backtest(utilities_sector, SmaCross,
              cash=10000, commission=.002)
bt_utilities.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          99.2608
Equity Final [$]                      4671.08
Equity Peak [$]                       19680.2
Return [%]                           -53.2892
Buy & Hold Return [%]                 306.811
Max. Drawdown [%]                    -87.8996
Avg. Drawdown [%]                    -41.5495
Max. Drawdown Duration     5883 days 00:00:00
Avg. Drawdown Duration      727 days 00:00:00
# Trades                                  285
Win Rate [%]                          39.6491
Best Trade [%]                        34.7309
Worst Trade [%]                      -22.1238
Avg. Trade [%]                      -0.140949
Max. Trade Duration         142 days 00:00:00
Avg. Trade Duration          26 days 00:00:00
Expectancy [%]                         3.1949
SQN                                  -1.00102
Sharpe Ratio                      

In [70]:
bt_utilities.plot()

In [65]:
health_sector = api.alpha_vantage.historic_quotes('XLV', adjusted=True, output_format='pandas')


In [66]:
health_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
health_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)

In [67]:
health_sector.sort_index(ascending=True, inplace=True)

In [68]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()

bt_health = Backtest(health_sector, SmaCross,
              cash=10000, commission=.002)
bt_health.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          99.1513
Equity Final [$]                      1348.66
Equity Peak [$]                       12313.7
Return [%]                           -86.5134
Buy & Hold Return [%]                 333.969
Max. Drawdown [%]                    -90.1164
Avg. Drawdown [%]                    -39.5644
Max. Drawdown Duration     7234 days 00:00:00
Avg. Drawdown Duration     2423 days 00:00:00
# Trades                                  270
Win Rate [%]                          35.9259
Best Trade [%]                        16.0721
Worst Trade [%]                      -22.1162
Avg. Trade [%]                      -0.650595
Max. Trade Duration         131 days 00:00:00
Avg. Trade Duration          27 days 00:00:00
Expectancy [%]                         3.0761
SQN                                  -2.75148
Sharpe Ratio                      

In [69]:
bt_health.plot()

In [71]:
tech_sector = api.alpha_vantage.historic_quotes('XLK', adjusted=True, output_format='pandas')


In [72]:
tech_sector.rename(columns={'1. open':'Open','2. high':'High','3. low':'Low', '5. adjusted close':'Close', '6. volume':'Volume'}, inplace=True)
tech_sector.drop(columns=['4. close','7. dividend amount', '8. split coefficient'], inplace=True)

In [73]:
tech_sector.sort_index(ascending=True, inplace=True)

In [74]:
class SmaCross(Strategy):
    def init(self):
        Close = self.data.Close
        self.ma1 = self.I(SMA, Close, 10)
        self.ma2 = self.I(SMA, Close, 20)

    def next(self):
        if crossover(self.ma1, self.ma2):
            self.buy()
        elif crossover(self.ma2, self.ma1):
            self.sell()

bt_tech = Backtest(tech_sector, SmaCross,
              cash=10000, commission=.002)
bt_tech.run()

Start                     2000-05-01 00:00:00
End                       2020-05-01 00:00:00
Duration                   7305 days 00:00:00
Exposure [%]                          99.1376
Equity Final [$]                      2738.06
Equity Peak [$]                       12778.6
Return [%]                           -72.6194
Buy & Hold Return [%]                 105.123
Max. Drawdown [%]                    -83.4173
Avg. Drawdown [%]                    -34.4158
Max. Drawdown Duration     6696 days 00:00:00
Avg. Drawdown Duration     1212 days 00:00:00
# Trades                                  250
Win Rate [%]                               36
Best Trade [%]                        27.4145
Worst Trade [%]                      -14.8777
Avg. Trade [%]                      -0.444858
Max. Trade Duration         145 days 00:00:00
Avg. Trade Duration          29 days 00:00:00
Expectancy [%]                        4.11764
SQN                                  -1.43809
Sharpe Ratio                      

In [75]:
bt_tech.plot()